In [1]:
import pandas as pd
import numpy as np 
import glob
import os 
from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font
from datetime import datetime

In [2]:
hoje = datetime.today().strftime('%Y-%m-%d')

In [3]:
# O QUE PRECISA PRA RODAR ESSE CÓDIGO:

# Arquivo Draft
# Arquivo Estoque
# Arquivo BI preço
# Arquivo pdv
# Arquivo Calendario
# Arquivo tabela de compra

#Atualizar o nome da marca no filtro do estoque.

In [4]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C10\TABELA DE PEDIDOS\Pedidos Semanais Especiais - BOT - 202510.xlsx")

df_tabela = df_tabela[df_tabela['Ação revendedor'].notna() | df_tabela['Ação consumidor'].notna()]

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm')]

#df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[(df_tabela['Categoria'] != "EMBALAGENS") | (df_tabela['Categoria'] != "SUPORTE À VENDA")]

df_tabela = df_tabela[df_tabela['Tipo de pedido'] == 'Semanal']

df_tabela = df_tabela[~df_tabela['Descrição'].str.contains('PRM')]

df_tabela = df_tabela[df_tabela['Tipo de produto']!= 'EDICAO LIMITADA']

df_tabela['Ação revendedor'] = np.where(df_tabela['Ação revendedor'].isna(),df_tabela['Ação consumidor'],df_tabela['Ação revendedor'])

df_tabela['Percentual de desconto revendedor'] = np.where(df_tabela['Percentual de desconto revendedor'].isna(),df_tabela['Percentual de desconto consumidor'],df_tabela['Percentual de desconto revendedor'])

df_tabela['MATCH'] = 1



In [5]:
df_tabela.columns

Index(['Ciclo', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Subcategoria', 'Quantidade por caixa', 'Tipo de promoção', 'Catálogo',
       'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'Sortimento P', 'Sortimento M',
       'Sortimento G', 'MATCH'],
      dtype='object')

In [6]:
df_tabela.shape

(702, 24)

In [7]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C09\arquivos pra gerar\pdvs\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C09\arquivos pra gerar\pdvs\PDV_ATT.xlsx")

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv[df_pdv['STATUS']!="INATIVO"]

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'STATUS'])

df_pdv['PDV'] = df_pdv['PDV DESC'].str.split("-").str[0].str.strip()

df_pdv = df_pdv[df_pdv['CANAL']!='MTZ']

#df_pdv['CANAL'] = np.where((df_pdv['CANAL']=='LJ')|(df_pdv['CANAL']=='HIB')|(df_pdv['CANAL']=='CD'),'TODOS','VD')

df_pdv['MATCH'] = 1



In [8]:
df_pdv = df_pdv.drop(columns=['pdv como texto','PDV DESC'])

In [9]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C11\atualização\DRAFT_"  # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)

df_draft.shape


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_54556\4129764549.py:10: DtypeWarning: Columns (7) have mixed types. Specify dtype option on import or set low_memory=False.
  df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


(114430, 46)

In [10]:
df_draft = df_draft.drop(columns=['Descrição','Compra inteligente semanal/Sugestão de compra',
       'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1','Planograma', 'Quantidade por caixa', 'Preço Sell In', 'Quantidade',
       'Item analisado', 'Subcategoria',
       'Lançamento', 'Desativação',
       'Promoção Próximo Ciclo', 'Categoria'])

In [11]:


# Caminho onde estão as subpastas com os arquivos CSV
pasta_entrada =  r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C11\atualização\estoque"

# Lista todas as subpastas dentro de "ESTOQUE"
subpastas = [os.path.join(pasta_entrada, d) for d in os.listdir(pasta_entrada) if os.path.isdir(os.path.join(pasta_entrada, d))]

df_list = []

# Percorre todas as subpastas
for subpasta in subpastas:
    arquivos = [f for f in os.listdir(subpasta) if f.endswith(".csv")]
    nome_pasta = os.path.basename(subpasta)  # Obtém o nome da pasta

    for arquivo in arquivos:
        caminho_arquivo = os.path.join(subpasta, arquivo)
        try:
            df = pd.read_csv(caminho_arquivo, encoding="utf-8", low_memory=False)  # Melhor para grandes volumes de dados
            df["Arquivo_Origem"] = arquivo  # Adiciona o nome do arquivo de origem
            df["Pasta_Origem"] = nome_pasta  # Adiciona o nome da pasta de origem
            df_list.append(df)
        except Exception as e:
            print(f"Erro ao ler o arquivo {arquivo}: {e}")

if df_list:
    df_estoque = pd.concat(df_list, ignore_index=True)

df_estoque['PDV'] = df_estoque['PDV'].astype(str)

df_estoque['SKU_FINAL'] = np.where(df_estoque['SKU_PARA'] == "-", df_estoque['SKU'], df_estoque['SKU_PARA'])

df_estoque['SKU_FINAL']=df_estoque['SKU_FINAL'].astype(str)


In [12]:
df_tabela.columns

Index(['Ciclo', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Subcategoria', 'Quantidade por caixa', 'Tipo de promoção', 'Catálogo',
       'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'Sortimento P', 'Sortimento M',
       'Sortimento G', 'MATCH'],
      dtype='object')

In [13]:
df_tabela = pd.merge(left=df_tabela,right=df_estoque[['SKU','SKU_FINAL']],left_on='Código',right_on='SKU',how='inner')

df_tabela['Código'] = df_tabela['SKU_FINAL']

df_tabela = df_tabela.drop(columns=['SKU','SKU_FINAL'])



In [14]:
df_estoque = df_estoque.drop(columns=['DESCRICAO', 'CATEGORIA', 'CLASSE', 'FASES PRODUTO',
       'LANCAMENTO', 'DESATIVACAO','COBERTURA ALVO',
       'ESTOQUE DE SEGURANCA','COBERTURA PROJETADA', 
       'Pasta_Origem'])

In [15]:
df_estoque

SKU SKU_PARA    PDV  ESTOQUE ATUAL  ESTOQUE EM TRANSITO  \
0       90495        -  20005          100.0                  0.0   
1       90246        -   4560            0.0                  NaN   
2       90246        -   5699            0.0                  NaN   
3       90246        -  12522            0.0                  NaN   
4       90246        -  12817            0.0                  NaN   
...       ...      ...    ...            ...                  ...   
441216   1594        -  20995            0.0                  0.0   
441217   1594        -  20998            0.0                  0.0   
441218   1594        -  21001            0.0                  0.0   
441219   1594        -  21278            0.0                  0.0   
441220   1594        -  21383            0.0                  0.0   

        PEDIDO PENDENTE  DDV PREVISTO  COBERTURA ATUAL  \
0                   0.0           NaN              NaN   
1                   0.0           NaN              NaN   
2                   0.0           NaN              NaN   
3                   0.0           NaN              NaN   
4                   0.0           NaN              NaN   
...                 ...           ...              ...   
441216              0.0           NaN              NaN   
441217              0.0           NaN              NaN   
441218              0.0           NaN              NaN   
441219              0.0           NaN              NaN   
441220              0.0           NaN              NaN   

        COBERTURA ATUAL + TRANSITO Arquivo_Origem SKU_FINAL  
0                              NaN        BOT.csv     90495  
1                              NaN        BOT.csv     90246  
2                              NaN        BOT.csv     90246  
3                              NaN        BOT.csv     90246  
4                              NaN        BOT.csv     90246  
...                            ...            ...       ...  
441216                         NaN        QDB.csv      1594  
441217                         NaN        QDB.csv      1594  
441218                         NaN        QDB.csv      1594  
441219                         NaN        QDB.csv      1594  
441220                         NaN        QDB.csv      1594  

[441221 rows x 11 columns]

In [16]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C09\arquivos pra gerar\preços bi\TABELA DE PREÇOS (4).xlsx")

df_bi_preco = df_bi_preco.drop(columns=['Descrição','Tipo Preço','CATEGORIA','LINHA','MARCA'])



c:\Users\joao.herculano\AppData\Local\Programs\Python\Python313\Lib\site-packages\openpyxl\styles\stylesheet.py:237: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [17]:
df_final = pd.merge(left=df_tabela,right=df_pdv,on='MATCH',how='inner')

df_final = df_final.drop_duplicates()

df_final.shape

(44744, 31)

In [18]:
df_final['PDV'] = df_final['PDV'].astype('Int64')
df_final['Código'] = df_final['Código'].astype('Int64')


df_final = pd.merge(left=df_final,right=df_draft,left_on=['PDV','Código'],right_on=['PDV','SKU'],how='left')
df_final.shape

(44744, 62)

In [19]:
df_final[(df_final['Código'] == 52023) & (df_final['PDV'] == 23712)]['Histórico de Vendas do Ciclo 202505']

26447    2.0
Name: Histórico de Vendas do Ciclo 202505, dtype: float64

In [20]:
df_final = df_final.drop(columns=['Sortimento P', 'Sortimento M',
       'Sortimento G','MARCA','SKU'])

In [21]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")


In [22]:
#ignorando a PDV que ainda não está online
df_pdv = df_pdv[df_pdv['DESCRIÇÃO PDV'] != '23813-COMERCIO-HIB VALENTE']

**ALTERAR NOME DA COLUNA "ARQUIVO_ORIGEM" PARA UMA DAS OPÇÕES ABAIXO:**

*BOT.csv* 

*EUD.csv*

*QDB.csv*

In [23]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario = calendario.drop(columns='MARCA')

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2) # >>>>>>>>> MUDAR PRA CICLO CORRETO 

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario


Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO       Date  NUM_CICLO  \
2199  C202510   2025-06-30 2025-07-20       21 2025-06-30         10   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2199     C2025    C202512               26

In [24]:
filtered_calendario['MATCH'] = 1

In [25]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [26]:
#df_tabela = df_tabela[(df_tabela['Tipo de promoção'] == "Revendedor" ) | (df_tabela['Tipo de promoção'] == "Promoções") |(df_tabela['Tipo de promoção'] == "Promoções | Revendedor" )]

In [27]:
df_draft['PDV'] = df_draft['PDV'].astype(str)

In [28]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','MATCH','dias_ate_inicio']], on='MATCH',how='inner')
df_final.shape

(44744, 62)

In [29]:
df_final['Código'] = df_final['Código'].astype('Int64') 
df_final['PDV'] = df_final['PDV'].astype('Int64') 

df_estoque['PDV'] = df_estoque['PDV'].astype('Int64') 
df_estoque['SKU_FINAL'] = df_estoque['SKU_FINAL'].astype('Int64') 

df_final = pd.merge(left=df_final,right=df_estoque,right_on=['PDV','SKU_FINAL'],left_on=['PDV','Código'],how='left')
df_final.shape

(54425, 72)

In [30]:
df_final['Código'] = df_final['Código'].astype('str')

df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype('str')

df_final = pd.merge(left=df_final,right=df_bi_preco,right_on=['UF','SKU2'],left_on=['UF','Código'],how='left')
df_final.shape   

(54425, 76)

In [31]:
df_bi_preco['SKU1'] = df_bi_preco['SKU1'].astype(str).str.replace('.0','',regex=False) 

df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],right_on=['UF','SKU1'],left_on=['UF','Código'],how='left')
df_final.shape   

(54514, 80)

In [32]:
df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [33]:
df_final['CANAL'] = np.where((df_final['CANAL'] == 'LJ') | (df_final['CANAL'] == 'HIB'), "TODOS" , np.where((df_final['CANAL'] == 'CD') | (df_final['CANAL'] == 'VD'), "VD", df_final['CANAL']))

df_final['CANAL'].value_counts()

CANAL
TODOS    42336
VD       12178
Name: count, dtype: int64

In [34]:
df_estoque = df_estoque.rename(columns={'SKU_FINAL':'SKU_PARA_VALIDACAO'})

df_estoque['SKU_PARA_VALIDACAO'] = df_estoque['SKU_PARA_VALIDACAO'].astype('Int64')

df_final = pd.merge( left= df_final, right = df_estoque[['SKU_PARA_VALIDACAO','Arquivo_Origem']], left_on= 'SKU', right_on='SKU_PARA_VALIDACAO', how='left')

df_final = df_final.drop_duplicates()

KeyboardInterrupt: 

In [ ]:
df_final = df_final.drop(columns=['SKU1_x','SKU1_y','SKU2_x','SKU2_y','PC_x', 'PV_x','PC_y', 'PV_y','Subcategoria',
'Carteira Bloqueada Para Novos Pedidos',
'Quantidade por caixa'
])

In [ ]:
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['SKU'].astype(str)


In [ ]:
df_final['Projeção Próximo Ciclo + 1'] =df_final['Projeção Próximo Ciclo + 1'] - df_final['Projeção Próximo Ciclo'] # projeção do ciclo em estudo

In [ ]:
df_final['Data Prevista Regularização'] = df_final['Data Prevista Regularização'].astype(str).replace('0','REGULAR')

In [ ]:
df_final = df_final.rename(columns={'Compra inteligente Próximo Ciclo + 1':'Compra inteligente Próximo Ciclo','Arquivo_Origem': 'MARCA'})

In [ ]:
df_final = df_final[~df_final['Marca'].isna()]
df_final['Marca'].isna().sum()

In [ ]:
df_final = df_final.drop_duplicates()
df_final.shape

In [ ]:
df_final[df_final.columns[26:43]] = df_final[df_final.columns[26:43]].fillna(0)


In [ ]:
df_final.columns[26:44]

In [ ]:
# Define list of target columns
sales_2024_cols = df_final.columns[26:44]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 2024'] = df_final[sales_2024_cols].max(axis=1)



In [ ]:
df_final.columns[37:44]

In [ ]:
vendas_6_meses = df_final.columns[37:44]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [ ]:
df_final.columns[37:44]

In [ ]:
# Define as colunas mensais
colunas_mensais = df_final.columns[26:43]

# Agrupa por PDV e calcula crescimento médio por PDV
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()             # soma por mês
    variacao_mensal = soma_mensal.pct_change().dropna()    # variação percentual mês a mês
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = df_final.groupby('PDV').apply(calcular_crescimento)

# Merge do resultado de volta no dataframe original
df_final = df_final.merge(crescimento_por_pdv, on='PDV', how='left')


In [ ]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[26:43]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO_GERAL'] = CRESCIMENTO

CRESCIMENTO


In [ ]:
vendas_todos_historicos = df_final.columns[26:44]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

medi = df_final.groupby(['CANAL'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})

df_final = pd.merge(left=df_final, right=medi,on='CANAL',how='inner')

medi

In [ ]:
df_final.columns[28:29].str.split(" ")[0][-1]

In [ ]:
mesmo_ciclo_ano_passado = df_final.columns[28:29]
ciclo_ano_passado = df_final.columns[28:29].str.split(" ")[0][-1]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [ ]:
df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'] #crescimento do pdv

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']>0.8,0.8,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']<0,0,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['MEDIANA DO HISTÓRICO'] = np.where(df_final['MEDIANA DO HISTÓRICO']==0,df_final['MEDIA DO HISTÓRICO'] ,df_final['MEDIANA DO HISTÓRICO'])

# Primeiro cálculo intermediário
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO_FINAL'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] <1,
                                    round(df_final['CRESCIMENTO_FINAL'] * df_final['MEDIANA DO HISTÓRICO']+ df_final['MEDIANA DO HISTÓRICO'],0), 
                                    round(df_final['CRESCIMENTO_FINAL']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado],0))


df_final.shape

In [ ]:
df_final.columns[26:39]

In [ ]:
df_final = df_final.rename(columns={df_final.columns[39]: "C-4", df_final.columns[40]: "C-3",df_final.columns[41]: "C-2",df_final.columns[42]: "C-1"})

In [ ]:
df_final.drop(columns=df_final.columns[26:39], inplace=True)


In [ ]:
# List all columns except the two
cols_to_group_by = df_final.columns.difference(['DDV PREVISTO', 'COBERTURA ATUAL'])

# Group and aggregate
df_final_dedup = (
    df_final
    .groupby(list(cols_to_group_by), dropna=False)[['DDV PREVISTO', 'COBERTURA ATUAL']]
    .max()
    .reset_index()
)


In [ ]:
df_final_dedup['DDV PREVISTO'] = df_final_dedup['DDV PREVISTO'].fillna(0.01)


In [ ]:
df_final_dedup[(df_final['PDV'] == 23712)]['C-3']

In [ ]:
df_final_dedup['DDV PREVISTO'] = np.where(
    df_final_dedup['DDV PREVISTO'] == 0,
    0.01,
    df_final_dedup['DDV PREVISTO']
)


In [ ]:
df_final_dedup.columns

In [ ]:
df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = (df_final_dedup['Estoque Atual'] + df_final_dedup['Estoque em Transito']) - round(df_final_dedup['dias_ate_inicio'] * df_final_dedup['DDV PREVISTO'],0)

In [ ]:
df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = np.where(df_final_dedup['EST PROJE FINAL CICLO ATUAL']<0,0,df_final_dedup['EST PROJE FINAL CICLO ATUAL'])

In [ ]:
df_final_dedup['VENDAS R$ PV GINSENG'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup['PV GINSENG']

In [ ]:
df_estoque.columns

In [ ]:
# Columns to bring up front
priority_cols = [
    'SKU',	'Marca',	'INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO',	'PRECO DE COMPRA',	'PRECO DE VENDA',
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'CANAL',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição',	'Categoria',
	'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',	'COBERTURA ATUAL',
    'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_final_dedup.columns if col not in priority_cols]

# Reorder
'Ação consumidor', 'Percentual de desconto consumidor', 'Ação revendedor', 'Percentual de desconto revendedor', '202408'


In [ ]:
#df_final_dedup = df_final_dedup[priority_cols + other_cols]


In [ ]:
df_final_dedup['RBV 202406'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup[ciclo_ano_passado] 

In [ ]:
df_final_dedup['COB PROJETADA'] = np.where(
    df_final_dedup['DDV PREVISTO'] != 0,
    (df_final_dedup['EST PROJE FINAL CICLO ATUAL'] + df_final_dedup['PV GINSENG']) / df_final_dedup['DDV PREVISTO'],
    999)


In [ ]:
df_final_dedup.drop(df_final_dedup.columns[39:40], axis=1, inplace=True)


In [ ]:
df_final_dedup.drop(columns=['dias_ate_inicio','SKU_FINAL',
                             'CRESCIMENTO'],inplace=True)

In [ ]:
df_final_dedup['MARCA'] = df_final_dedup['MARCA'].str.replace('.csv','',regex=False)

In [ ]:
df_final_dedup['COB PROJETADA'] = df_final_dedup['COB PROJETADA'].fillna(999)

In [ ]:
marca_promo =  df_estoque['Arquivo_Origem'].iloc[0].replace('.csv','')
marca_promo

In [ ]:
df_final_dedup['INICIO CICLO'] = pd.to_datetime(df_final_dedup['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_final_dedup['FIM CICLO'] = pd.to_datetime(df_final_dedup['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [ ]:
df_final_dedup['Percentual de desconto revendedor'] = np.where((df_final_dedup['Percentual de desconto revendedor'].isna()) & (~df_final_dedup['Percentual de desconto consumidor'].isna()),df_final_dedup['Percentual de desconto consumidor'],df_final_dedup['Percentual de desconto revendedor'])

In [ ]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype('Int64')
df_final_dedup['PDV'] = df_final_dedup['PDV'].astype('Int64')


df_final_dedup = pd.merge(left=df_final_dedup,right=df_pdv_origi[['PDV','CANAL','UF']],how='inner',on='PDV')

In [ ]:
df_vdc = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C10\VENDA VITORIA 2024\VENDA VITORIA.csv")

df_vdc['PRODUTO'] = df_vdc['PRODUTO'].astype('Int64')

df_final_dedup['Código'] = df_final_dedup['Código'].astype('Int64')

df_final_dedup =pd.merge(left=df_final_dedup,right=df_vdc[['PDV GINSENG','PRODUTO',ciclo_ano_passado]],left_on= ['PDV','Código'],right_on= ['PDV GINSENG','PRODUTO'],how='left' )

df_final_dedup['202410_y'] = df_final_dedup['202410_y'].fillna(0)

In [ ]:
df_final_dedup.head()

In [ ]:
df_final_dedup['202410_x'] = np.where(df_final_dedup['202410_y']>0,df_final_dedup['202410_y'],df_final_dedup['202410_x'])

In [ ]:
df_final_dedup = df_final_dedup.drop(columns=['Arquivo_Origem_x','Arquivo_Origem_y','CANAL_x','Canal',
                                              'Ciclo_x','Ciclo_y','DURAÇÃO','FIM CICLO','Foco','INICIO CICLO','MATCH',
                                              'PRECO DE COMPRA','SKU','SKU_PARA','SKU_PARA_VALIDACAO',
                                              'Tipo de pedido',	'Tipo de produto','UFPRODUTO','Unidade de negócio','EST PROJE FINAL CICLO ATUAL',
                                              'UF_x','RBV 202406','Região','Catálogo','SKU','VENDAS R$ PV GINSENG','Data Prevista Regularização',
                                              'IAF', 'Item Desativado','Tipo de promoção','PDV GINSENG','PRODUTO','202410_y',
                                              'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO','COBERTURA ATUAL + TRANSITO',
                                              'DDV PREVISTO',	'COB PROJETADA','COBERTURA ATUAL',
                                              'CRESCIMENTO_FINAL',	'CRESCIMENTO_GERAL','med_por_canal','PEDIDO PENDENTE'])

In [ ]:
df_final_dedup = df_final_dedup.rename(columns={'CANAL_y':'CANAL','UF_y':'UF','Marca':'LINHA','202410_x':'202410'})


In [ ]:
df_final_dedup.columns

In [ ]:
df_final_dedup[(df_final['PDV'] == 23712)]['C-3']

In [ ]:
priority_cols = ['SUPERVISOR','ANALISTA','UF','CANAL','LINHA','PDV','DESCRIÇÃO PDV','Código','Descrição','Categoria', 
'Classe','Percentual de desconto consumidor','Ação consumidor','Percentual de desconto revendedor','Ação revendedor','C-1',
'C-2', 'C-3', 'C-4','Histórico de Vendas do Ciclo Atual','Estoque Atual','Estoque em Transito','Pedido Pendente',
'Projeção Próximo Ciclo + 1','Projeção Próximo Ciclo']

# All remaining columns
other_cols = [col for col in df_final_dedup.columns if col not in priority_cols]

# Reorder
df_final_dedup = df_final_dedup[priority_cols + other_cols]

df_final_dedup['SUGESTÃO ABASTECIMENTO'] = ''


In [ ]:
df_final_dedup = df_final_dedup.drop_duplicates()

In [ ]:
df_final_dedup['PV GINSENG'].sum()

In [ ]:
df_final_dedup[df_final_dedup['PDV'] == 23712]['PICO DE VENDAS 2024'].isna().sum()

In [ ]:
# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\promoção_{marca_promo}_{ciclo_mais2}.{hoje}.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_final_dedup.to_excel(writer, index=False)

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL